Install necessary files

In [2]:
# import packages for analysis and modeling
!pip install fiona
!pip install geopandas
import pandas as pd #data frame operations
import numpy as np #arrays and math functions
from scipy.stats import uniform #for training and test splits
import statsmodels.api as smf #R-like model specification
import matplotlib.pyplot as plt #2D plotting
import requests
import folium
import sys
import math
from folium.plugins import FeatureGroupSubGroup
from folium.plugins import MarkerCluster
import geopandas as gpd
from shapely.geometry import Point
from folium.plugins import MeasureControl
from datetime import datetime
from folium.plugins import TimestampedGeoJson

     |████████████████████████████████| 14.8MB 318kB/s 
     |████████████████████████████████| 972kB 11.1MB/s 
     |████████████████████████████████| 6.5MB 30.3MB/s 


/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


Pull in and clean dataframes

In [5]:
albania = pd.read_csv("/content/drive/MyDrive/albania/conflict_data_alb.csv")
albania.rename(columns=albania.iloc[0]).drop(albania.index[0])
albania.columns=['data.id', 'ISO', 'event.code', 'event.id.city', 'event_date', 'event_year', 'timeprecision', 'event_type', 'subeventtype', 'actor1', 'assoc.actor1', 'inter1', 'actor1', 'assoc2','inter2','interaction', 'region', 'country', 'admin1', 'admin2', 'admin3', 'loc.name', 'latitude', 'longitude', 'geoprecision', 'source', 'source.scale', 'notes', 'fatalities', 'timestamp', 'countrycode']
albania=albania.drop(albania.index[[0]])
albania=albania[['event_date', 'event_year', 'event_type', 'subeventtype', 'actor1', 'assoc.actor1', 'actor1', 'assoc2', 'admin1', 'admin2', 'admin3', 'loc.name', 'latitude', 'longitude', 'source', 'source.scale', 'notes']]
albania['longitude']=albania['longitude'].astype(float)
albania['latitude']=albania['latitude'].astype(float)
x=np.unique(albania.event_type)
#albania.info()
#albania.head()
viol=albania[~albania["event_type"].isin(["Strategic developments", "Protests"])]
peace=albania[albania["event_type"].isin(["Strategic developments", "Protests"])]
albania["event_date"]=pd.to_datetime(albania["event_date"])
#albania['event_date'] = albania['event_date'].dt.strftime('%Y-%m-%d')
twenty=albania[albania["event_year"]=="2020"]
twenty1=albania[albania["event_year"]=="2021"]
ninteen=albania[albania["event_year"]=="2019"]
eighteen=albania[albania["event_year"]=="2018"]
albania.info()
albania.head()
albania.to_csv(r'albania.csv', index = False)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 825 entries, 1 to 825
Data columns (total 19 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   event_date    825 non-null    datetime64[ns]
 1   event_year    825 non-null    object        
 2   event_type    825 non-null    object        
 3   subeventtype  825 non-null    object        
 4   actor1        825 non-null    object        
 5   actor1        140 non-null    object        
 6   assoc.actor1  507 non-null    object        
 7   actor1        825 non-null    object        
 8   actor1        140 non-null    object        
 9   assoc2        35 non-null     object        
 10  admin1        825 non-null    object        
 11  admin2        825 non-null    object        
 12  admin3        1 non-null      object        
 13  loc.name      825 non-null    object        
 14  latitude      825 non-null    float64       
 15  longitude     825 non-null    float64   

Create a Map to demonstrate Albanian Sigacts with a switch for Violent and Non Violent Events.

In [71]:
eventmap = folium.Map(
    location=[41.00, 20.00],
    zoom_start=8,
    tiles='cartodbdark_matter'
)


mcg=folium.plugins.MarkerCluster(name="Event Type", control=False)
eventmap.add_child(mcg)

#fg2=folium.plugins.MarkerCluster(name="Year", control=False)
#eventmap.add_child(fg2)

def color(event):
  if event == "Protests": 
    col='blue'
  elif event=="Strategic developments":
    col='green'
  else:
    col='red'
  return col

def icon(event):
  if event == "Protests": 
    icon='fa-bullhorn'
  elif event=="Strategic developments":
    icon='fa-bullseye'
  else:
    icon='fa-bomb'
  return icon

marker_cluster=folium.plugins.FeatureGroupSubGroup(mcg, 'Violence')
eventmap.add_child(marker_cluster)
marker_cluster1=folium.plugins.FeatureGroupSubGroup(mcg, 'Nonviolence')
eventmap.add_child(marker_cluster1)
'''marker_cluster2=folium.plugins.FeatureGroupSubGroup(mcg, '2020')
eventmap.add_child(marker_cluster2)
marker_cluster3=folium.plugins.FeatureGroupSubGroup(mcg, '2021')
eventmap.add_child(marker_cluster3)
marker_cluster4=folium.plugins.FeatureGroupSubGroup(mcg, '2018')
eventmap.add_child(marker_cluster4)
marker_cluster5=folium.plugins.FeatureGroupSubGroup(mcg, '2019')
eventmap.add_child(marker_cluster5)'''
for _, row in viol.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster)


for _, row in peace.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster1)

'''for _, row in twenty.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster2)'''


'''for _, row in twenty1.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster3)'''

'''for _, row in eighteen.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster4)'''


'''for _, row in ninteen.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster5)'''            
folium.TileLayer("OpenStreetMap").add_to(eventmap)
folium.LayerControl().add_to(eventmap)
eventmap


Created a similar map for exploring the data with a filter for year of event occurence.

In [70]:
eventmap2 = folium.Map(
    location=[41.00, 20.00],
    zoom_start=8,
    tiles='OpenStreetMap'
)


mcg=folium.plugins.MarkerCluster(name="Event Type", control=False)
eventmap2.add_child(mcg)

#fg2=folium.plugins.MarkerCluster(name="Year", control=False)
#eventmap.add_child(fg2)

def color(event):
  if event == "Protests": 
    col='blue'
  elif event=="Strategic developments":
    col='green'
  else:
    col='red'
  return col

def icon(event):
  if event == "Protests": 
    icon='fa-bullhorn'
  elif event=="Strategic developments":
    icon='fa-bullseye'
  else:
    icon='fa-bomb'
  return icon

'''marker_cluster=folium.plugins.FeatureGroupSubGroup(mcg, 'Violence')
eventmap.add_child(marker_cluster)
marker_cluster1=folium.plugins.FeatureGroupSubGroup(mcg, 'Nonviolence')
eventmap.add_child(marker_cluster1)'''
marker_cluster2=folium.plugins.FeatureGroupSubGroup(mcg, '2020')
eventmap2.add_child(marker_cluster2)
marker_cluster3=folium.plugins.FeatureGroupSubGroup(mcg, '2021')
eventmap2.add_child(marker_cluster3)
marker_cluster4=folium.plugins.FeatureGroupSubGroup(mcg, '2018')
eventmap2.add_child(marker_cluster4)
marker_cluster5=folium.plugins.FeatureGroupSubGroup(mcg, '2019')
eventmap2.add_child(marker_cluster5)
'''for _, row in viol.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster)'''


'''for _, row in peace.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster1)'''

for _, row in twenty.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster2)


for _, row in twenty1.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster3)

for _, row in eighteen.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster4)


for _, row in ninteen.iterrows():
  html="""<i>Location: </i> <br> <b>{}</b> <br> 
                  <i>Date: </i><b><br>{}</b><br>
                  <i>Description: </i><b><br>{}</b><br>""".format(
                    row['loc.name'], 
                    row['event_date'], 
                    row['notes'])
  iframe=folium.IFrame(html, width=200, height=300)
  popup = folium.Popup(iframe,
                     max_width=500)
  marker=folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup,
        icon=folium.Icon(color=color(row['event_type']), icon=icon(row['event_type']), prefix='fa', icon_color='black')).add_to(marker_cluster5)            
folium.TileLayer("cartodbdark_matter").add_to(eventmap2)
folium.LayerControl().add_to(eventmap2)
eventmap2